In [1]:
import os
import pandas as pd
import glob
from collections import Counter

folder_path = "outputs/kaggle_results/"

prefix = "response_clean"


# Step 1: Set up folder and file pattern
pattern = os.path.join(folder_path, f"{prefix}*.csv")
csv_files = glob.glob(pattern)

# Step 2: Identify main file and other files
main_file = [f for f in csv_files if 'jun26_1158' in f][0]
other_files = [f for f in csv_files if f != main_file]

# Step 2: Read and split "ID\tlabel" column into two columns: ID, label
dfs = []
def load_and_split(file):
    df = pd.read_csv(file)
    return df

dfs = [load_and_split(file) for file in csv_files]
main_df = load_and_split(main_file)
other_dfs = [load_and_split(file) for file in other_files]

# Step 4: Concatenate other files for majority voting
other_data = pd.concat(other_dfs)

# Step 5: Group by ID and get all labels (for checking if all disagree)
other_labels = other_data.groupby("ID")["label"].apply(list)

# Step 6: Merge with main_df to align labels
main_df = main_df.merge(other_labels, on="ID", how="left")  # Now has 'label_x' and 'label_y'

# Rename for clarity
main_df = main_df.rename(columns={"label_x": "main_label", "label_y": "other_labels"})

# Step 7: Apply conditional rule
def decide_label(row):
    main_label = row['main_label']
    other_votes = row['other_labels']
    if other_votes and all(label != main_label for label in other_votes):
        # Override with majority vote
        return Counter(other_votes).most_common(1)[0][0]
    else:
        return main_label

main_df['final_label'] = main_df.apply(decide_label, axis=1)

# Step 8: Build final result
final_df = main_df[['ID', 'final_label']].rename(columns={'final_label': 'label'})
best_df = pd.read_csv("outputs/kaggle_results/response_clean_jun26_1158.csv")

In [2]:
unver_list = [index for index in range(len(best_df)) if best_df.at[index, "label"] == "unver"]

unver_list

[1,
 6,
 14,
 17,
 23,
 26,
 29,
 30,
 31,
 32,
 36,
 37,
 41,
 42,
 46,
 47,
 49,
 51,
 53,
 58,
 59,
 62,
 63,
 68,
 69,
 71,
 72,
 77,
 79,
 80,
 84,
 85,
 87,
 88,
 91,
 92,
 94,
 95,
 98,
 102,
 104,
 106,
 108,
 110,
 111,
 113,
 114,
 115,
 116,
 120,
 122,
 123,
 124,
 125,
 130,
 131,
 133,
 134,
 135,
 137,
 139,
 142,
 144,
 145,
 146,
 148,
 150,
 153,
 155,
 156,
 158,
 159,
 163,
 165,
 166,
 168,
 170,
 175,
 176,
 177,
 178,
 180,
 182,
 185,
 186,
 188,
 189,
 191,
 192,
 193,
 195,
 196,
 198,
 199,
 200,
 203,
 205,
 206,
 207,
 209,
 210,
 212,
 224,
 225,
 226,
 230,
 235,
 236,
 238,
 239,
 241,
 242,
 243,
 245,
 247,
 248,
 250,
 253,
 257,
 258,
 260,
 262,
 263,
 264,
 265,
 275,
 276,
 277,
 279,
 280,
 283,
 284,
 285,
 286,
 287,
 288,
 291,
 292,
 293,
 295,
 296,
 298,
 304,
 305,
 308,
 309,
 313,
 314,
 315,
 316,
 317,
 320,
 323,
 324,
 326,
 327,
 332,
 333,
 334,
 335,
 338,
 343,
 344,
 346,
 347,
 350,
 353,
 355,
 356,
 359,
 360,
 361,
 364,
 36

In [3]:
import asyncio
import os
import networkx as nx

from dotenv import load_dotenv
from operationCheatSheet import chunking_by_token_size, extract_entities, extract_evidence
from utils import compute_mdhash_id
from geminillm import gemini_complete_if_cache
from openaillm import openai_embed, openai_complete
from faiss_impl import FaissVectorDBStorage
from networkx_impl import NetworkXStorage
from json_kv_iml import JsonKVStorage
from shared_storage import initialize_share_data
from cheatsheet import CHEATSHEETS


# LLM_MODEL_NAME = "gpt-3.5-turbo"
LLM_MODEL_NAME = "gemini-2.5-flash-preview-05-20"

load_dotenv()

async def process_text_to_knowledge_graph_on_reference(text_content,
                                          cheatsheet_knowledge_graph_inst,
                                          seed_entities,
                                          max_gleaning = 1,
                                          file_path="unknown_source",
                                          prefix=""
                                          ):
    # Step 1: Create chunks from your text content
    raw_chunks = chunking_by_token_size(
        content=text_content,
        split_by_character=None,  # Optional: specify a character to split by (e.g., "\n\n")
        split_by_character_only=False,
        overlap_token_size=128,
        max_token_size=1024,
        tiktoken_model=LLM_MODEL_NAME
    )
    
    # Step 2: Format chunks as required by extract_entities
    doc_id = compute_mdhash_id(text_content, prefix="doc-")
    chunks = {
        compute_mdhash_id(chunk["content"], prefix="chunk-"): {
            **chunk,
            "full_doc_id": doc_id,
            "file_path": file_path
        }
        for chunk in raw_chunks
    }
    
    # Step 3: Initialize your storage instances
    faiss_global_config = {
        "working_dir": "/tmp",
        "embedding_batch_num": 64,  # or another integer suitable for your setup
        "vector_db_storage_cls_kwargs": {
            "cosine_better_than_threshold": 0.2  # or another float threshold you want
        },
        "base_url": "https://api.openai.com/v1",
    }
    kv_global_config = {
        "working_dir": "/tmp",
        "llm_model_name": LLM_MODEL_NAME,
        "embedding_batch_num": 64,  # or another integer suitable for your setup
        "vector_db_storage_cls_kwargs": {
            "cosine_better_than_threshold": 0.2  # or another float threshold you want
        },
        "base_url": "https://api.openai.com/v1",
    }
    knowledge_graph = NetworkXStorage(namespace="nx_kg", global_config=faiss_global_config, embedding_func=openai_embed)  # Graph storage implementation
    entity_vector_db = FaissVectorDBStorage(namespace="faiss_entity", global_config=faiss_global_config, embedding_func=openai_embed)  # Vector storage for entities
    relationship_vector_db = FaissVectorDBStorage(namespace="faiss_relationship", global_config=faiss_global_config, embedding_func=openai_embed)  # Vector storage for relationships
    llm_cache = JsonKVStorage(namespace="llm_cache", global_config=kv_global_config, embedding_func=openai_embed)
    
    initialize_share_data()

    await knowledge_graph.initialize()
    await entity_vector_db.initialize()
    await relationship_vector_db.initialize()
    await llm_cache.initialize()  # if your cache supports/needs it

    # Step 4: Use the OpenAI LLM function from openai.py
    # Create a wrapper that matches the expected signature for extract_entities
    async def llm_wrapper(prompt, history_messages=None, max_tokens=None, **kwargs):
        if history_messages is None:
            history_messages = []
    

        # Use Google GenAI
        return await gemini_complete_if_cache(
            model=LLM_MODEL_NAME,
            prompt=prompt,
            history_messages=history_messages,
            hashing_kv=llm_cache,
            temperature=0.2,
            max_tokens=max_tokens or 1024,
        )
    
    # Step 5: Configure the extraction process
    global_config = {
        "llm_model_func": llm_wrapper,  # Use our wrapper function
        "llm_model_name": LLM_MODEL_NAME,  # Required for some OpenAI functions
        "entity_extract_max_gleaning": max_gleaning,
        "force_llm_summary_on_merge": False,
        "llm_model_max_token_size": 1024,
        "summary_to_max_tokens": 256,
        "tiktoken_model_name": LLM_MODEL_NAME,
        "addon_params": {
            "language": "English",
            "entity_types": [
                "Software or Computational Method",
                "Scientific Method",
                "Infrastructure or Equipment",
                "Institution or Organization",
                "Ecological or Biological Entity",
                "Pollutant or Material",
                "Time Expression",
                "Health or Disease Concept",
                "Food or Nutrition Element",
                "Demographic Group",
                "Measurement or Quantity"
            ]
        },
    }
    
    # Step 6: Optional status tracking
    pipeline_status = {
        "latest_message": "",
        "history_messages": []
    }
    pipeline_status_lock = asyncio.Lock()
    
    # Step 7: Run the extraction
    await extract_evidence(
        chunks=chunks,
        knowledge_graph_inst=knowledge_graph,
        entity_vdb=entity_vector_db,
        relationships_vdb=relationship_vector_db,
        global_config=global_config,
        seed_entities=seed_entities,
        pipeline_status=pipeline_status,
        pipeline_status_lock=pipeline_status_lock,
        llm_response_cache=llm_cache,
        cheatsheet_knowledge_graph_inst=cheatsheet_knowledge_graph_inst,
        write_result_to_txt=True,
        special_interest=CHEATSHEETS["special_interests"],
        prefix=prefix
    )
    
    return knowledge_graph


# Example usage in a Jupyter notebook
async def run_on_reference(content, nx_graph, seed_entities, max_gleaning, prefix=""):
    # monkeyReader = reader.MonkeyReader('monkey') # or 'lxml' or 'x2d'

    # read paper content
    # essay = monkeyReader.readEssay('./xmldata/Byjesh.pdf.tei.xml')
    # text = "\n".join(essay["Impact of fixed rise in temperature, CO 2 and change in rain fall"])
    text = content
    # nx_graph = nx.Graph()
    knowledge_graph = await process_text_to_knowledge_graph_on_reference(text,
                                                                         nx_graph,
                                                                         seed_entities,
                                                                         max_gleaning,
                                                                         "example.txt",
                                                                         prefix=prefix)
    # Now you can query the knowledge graph for entities and relationships
    
    return knowledge_graph

In [4]:
import networkx as nx
from utils import get_latest_result, read_knowledge_graph_from_pickle

async def get_othology_graph(entity_nodes, entity_edges):
    G = nx.Graph()
    for edge_keys, edge_list in entity_edges.items():
        for edge in edge_list:
            source = edge.get("src_id", "")
            target = edge.get("tgt_id", "")
            if source and target:
                if source in entity_nodes and target in entity_nodes:
                    G.add_edge(
                        entity_nodes[source][0]["entity_type"],
                        entity_nodes[target][0]["entity_type"],
                    )
    return G

In [5]:
import pandas as pd

from geminillm import gemini_complete_if_cache
from json_kv_iml import JsonKVStorage
from operationCheatSheet import preprocessing_claim
from openaillm import openai_embed

LLM_MODEL_NAME = "gemini-2.5-flash-preview-05-20"

TASKNAMES = ["subtask1", "subtask2"]
TYPES = ["test", "test_preprocess"]

dataset_loader = dict()

for taskname in TASKNAMES:
    for type in TYPES:
        print(f"Processing {taskname} for {type}")
        prefix = "dataset"
        # Load the data
        
        if taskname == "subtask2" and type == "test_preprocess":
            continue
        data = pd.read_csv(f"{prefix}/{taskname}_{type}.csv")
        dataset_loader[f"{taskname}_{type}"] = data

dataset_loader["subtask1_test"]["claim"] = dataset_loader["subtask1_test_preprocess"]["claim"]

Processing subtask1 for test
Processing subtask1 for test_preprocess
Processing subtask2 for test
Processing subtask2 for test_preprocess


In [6]:
from utils import get_latest_result_by_prefix
from tqdm import trange, tqdm

test_data = dataset_loader["subtask1_test"]
for index in tqdm(unver_list):
    reference_content = test_data.at[index, "reference"]
    claim_nodes, claim_edges = await get_latest_result_by_prefix(f"claim_test_{index}_result")
    claim_ontology_graph = await get_othology_graph(claim_nodes, claim_edges)
    seed_entities = list(claim_nodes.keys())

    _ = await run_on_reference(reference_content,
                               claim_ontology_graph,
                               seed_entities, 2, prefix=f"reference_test_{index}")

  0%|          | 0/483 [00:00<?, ?it/s]No existing Faiss index file found. Starting fresh.
No existing Faiss index file found. Starting fresh.
INFO: Process 43829 Shared-Data created for Single Process
INFO: Process 43829 initialized updated flags for namespace: [nx_kg]
INFO: Process 43829 initialized updated flags for namespace: [faiss_entity]
INFO: Process 43829 initialized updated flags for namespace: [faiss_relationship]
INFO: Process 43829 initialized updated flags for namespace: [llm_cache]
INFO: Process 43829 ready to initialize storage namespace: [llm_cache]
/home/com3dian/Github/meta-knowledge-harvesting-llm/kaggle/operationCheatSheet.py:1231: RuntimeWarning: coroutine 'extract_evidence.<locals>.nightly_kg_to_text' was never awaited
  hint_prompt = fill_nightly_prompt.format(


Final result:
("entity"<|>"Agricultural Productivity"<|>"Agricultural Productivity"<|>"Measurement or Quantity"<|>"Agricultural productivity has trebled in Australia over the last 50 years, suggesting that all is well in the heartland of agriculture - the inland rural communities around which much of our production is based."<|>"Agricultural productivity has trebled"<|>7<|>"")##
("entity"<|>"Last 50 Years"<|>"Last 50 Years"<|>"Time Expression"<|>"Agricultural productivity has trebled in Australia over the last 50 years, suggesting that all is well in the heartland of agriculture - the inland rural communities around which much of our production is based."<|>"over the last 50 years"<|>7<|>"")##
("entity"<|>"Inland Rural Communities"<|>"Inland Rural Communities"<|>"Infrastructure or Equipment"<|>"Agricultural productivity has trebled in Australia over the last 50 years, suggesting that all is well in the heartland of agriculture - the inland rural communities around which much of our pro

  0%|          | 1/483 [01:59<15:57:51, 119.24s/it]No existing Faiss index file found. Starting fresh.
No existing Faiss index file found. Starting fresh.
INFO: Process 43829 Shared-Data already initialized (multiprocess=False)
INFO: Process 43829 storage namespace already initialized: [llm_cache]


Final result:
("entity"<|>"Chronic Wound"<|>"Chronic Wound"<|>"Health or Disease Concept"<|>"The major problems in patients with chronic wounds include pain, abundant exudate that may frequently be difficult to control, bad odor, occasionally bleeding, and wound infection, the latter predominantly in diabetic patients."<|>"chronic wound"<|><|>)##
("entity"<|>"Support Dressing"<|>"Support Dressing"<|>"Infrastructure or Equipment"<|>"Appropriate choice of support dressing for the treatment and topical care of chronic wound is one of the crucial factors in the management of this type of wounds, especially if thus ensuring maximal action upon the etiological causative agent."<|>"support dressing"<|><|>)##
("entity"<|>"Topical Care"<|>"Topical Care"<|>"Scientific Method"<|>"Appropriate choice of support dressing for the treatment and topical care of chronic wound is one of the crucial factors in the management of this type of wounds, especially if thus ensuring maximal action upon the etiol

  0%|          | 2/483 [04:00<16:03:49, 120.23s/it]No existing Faiss index file found. Starting fresh.
No existing Faiss index file found. Starting fresh.
INFO: Process 43829 Shared-Data already initialized (multiprocess=False)
INFO: Process 43829 storage namespace already initialized: [llm_cache]


...

100%|█████████▉| 481/483 [22:21:45<05:52, 176.30s/it]No existing Faiss index file found. Starting fresh.
No existing Faiss index file found. Starting fresh.
INFO: Process 43829 Shared-Data already initialized (multiprocess=False)
INFO: Process 43829 storage namespace already initialized: [llm_cache]


Final result:
("entity"<|>"Agile Development Methods"<|>"Software or Computational Method"<|>"Agile development methods have emerged to overcome some of the process and product-related problems associated with traditional models. They are believed to be lightweight, people focused, adaptive and allow better information systems development (ISD) performance. Agile software development methods have a number of reported benefits on productivity, project visibility, software quality and other areas. Agile development methods and their associated practices have become well-accepted within industry, and the success of projects using these methods is higher than traditional methods [1]."<|>"Agile development methods"<|>[1], [6], [9]<|>")##
("entity"<|>"Traditional Models"<|>"Software or Computational Method"<|>"Agile development methods have emerged to overcome some of the process and product-related problems associated with traditional models. The success of projects using these methods is h

100%|█████████▉| 482/483 [22:24:01<02:44, 164.18s/it]No existing Faiss index file found. Starting fresh.
No existing Faiss index file found. Starting fresh.
INFO: Process 43829 Shared-Data already initialized (multiprocess=False)
INFO: Process 43829 storage namespace already initialized: [llm_cache]


Final result:
("entity"<|>"Imbalance Data (Definition)"<|>"Imbalance Data (Definition)"<|>"Software or Computational Method"<|>"Imbalance data are defined as a dataset whose proportion of classes is severely skewed."<|>"Imbalance data"<|>[2]<|>"")##
("entity"<|>"Classification Performance"<|>"Classification Performance"<|>"Measurement or Quantity"<|>"Classification performance of existing models tends to deteriorate due to class distribution imbalance."<|>"Classification performance"<|>[2]<|>"")##
("entity"<|>"RHSBoost"<|>"RHSBoost"<|>"Software or Computational Method"<|>"An effective ensemble classification method called RHSBoost has been proposed to address the imbalance classification problem."<|>"RHSBoost"<|>[2]<|>"")##
("entity"<|>"Random Undersampling"<|>"Random Undersampling"<|>"Software or Computational Method"<|>"This classification rule uses random undersampling and ROSE sampling under a boosting scheme."<|>"random undersampling"<|>[2]<|>"")##
("entity"<|>"ROSE Sampling"<|>"R

100%|██████████| 483/483 [22:26:56<00:00, 167.32s/it]
